In [ ]:
from transformers import pipeline
from termcolor import colored
import torch

In [ ]:
# !pip install termcolor==1.1.0

In [ ]:
class Ner_Extractor:
    
    def __init__(self, model_checkpoint):
        
        self.token_pred_pipeline = pipeline("token-classification", 
                                            model=model_checkpoint, 
                                            aggregation_strategy="average")
    
    @staticmethod
    def text_color(txt, txt_c="blue", txt_hglt="on_yellow"):
        return colored(txt, txt_c, txt_hglt)
    
    @staticmethod
    def concat_entities(ner_result):
        
        entities = []
        prev_entity = None
        prev_end = 0
        for i in range(len(ner_result)):
            if (ner_result[i]["entity_group"] == prev_entity) &\
               (ner_result[i]["start"] == prev_end):
                entities[i-1][2] = ner_result[i]["end"]
                prev_entity = ner_result[i]["entity_group"]
                prev_end = ner_result[i]["end"]
            else:
                entities.append([ner_result[i]["entity_group"], 
                                 ner_result[i]["start"], 
                                 ner_result[i]["end"]])
                prev_entity = ner_result[i]["entity_group"]
                prev_end = ner_result[i]["end"]
        
        return entities
    
    
    def colored_text(self, text, entities):
        
        colored_text = ""
        init_pos = 0
        for ent in entities:
            if ent[1] > init_pos:
                colored_text += text[init_pos: ent[1]]
                colored_text += self.text_color(text[ent[1]: ent[2]]) + f"({ent[0]})"
                init_pos = ent[2]
            else:
                colored_text += self.text_color(text[ent[1]: ent[2]]) + f"({ent[0]})"
                init_pos = ent[2]
        
        return colored_text
    
    
    def get_entities(self, text: str):
        
        entities = self.token_pred_pipeline(text)
        concat_ent = self.concat_entities(entities)
        
        return concat_ent
    
    
    def show_ents_on_text(self, text: str):
        
        entities = self.get_entities(text)
        
        return self.colored_text(text, entities)

In [ ]:
seqs_example = ["Из Дзюбы вышел бы отличный бразилец». Интервью Клаудиньо",
"Самый яркий бразилец «Зенита» рассказал о встрече с Пеле, страшном морозе в Самаре и любимых финтах Роналдиньо",
"Стали известны подробности нового иска РФС к УЕФА и ФИФА",
"Реванш «Баварии», голы от «Реала» с «Челси»: ставим на ЛЧ",
"Кварацхелия не вернется в «Рубин» и станет игроком «Наполи»",
"«Манчестер Сити» сделал грандиозное предложение по Холанду",
"В России хотят возродить Кубок лиги. Он проводился в 2003 году",
"Экс-футболиста сборной Украины уволили с ТВ за слова о россиянах",
"Экс-игрок «Реала» находится в критическом состоянии после ДТП",
"Аршавин посмеялся над показателями Глушакова в игре с ЦСКА",
"Арьен Роббен пробежал 42-километровый марафон",
"Бывший игрок «Спартака» предложил бить футболистов палками"]

In [ ]:
%%time
extractor = Ner_Extractor(model_checkpoint = "surdan/LaBSE_ner_nerel")

In [ ]:
%%time
show_entities_in_text = (extractor.show_ents_on_text(i) for i in seqs_example)

In [ ]:
%%time
l_entities = [extractor.get_entities(i) for i in seqs_example]
len(l_entities), len(seqs_example)

In [ ]:
for i in range(len(seqs_example)):
    print(next(show_entities_in_text, "End of generator"))
    print("-*-"*25)